# Imports

In [1]:
import sys
from sklearn.metrics import classification_report, accuracy_score, f1_score
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
import numpy as np
import itertools
from itertools import product
import pprint
import sys
import functools as ft
from sklearn.utils import shuffle

In [2]:
sys.path.append('Code/')
from single_split_gridsearch import SingleSplitGridSearch

In [2]:
FATOR_TEST = 2
FATOR_TREINO = 2

features_folder = '../datasets/'

folds = [1, 2, 3, 4, 5]
patches = [1, 3, 5, 10]

# Loads e Predictions

In [4]:
def get_tensor(features, labels, n_patches):
  inicio= 0
  ty = []
  tx = []

  for i in range(0, len(features)+1, n_patches):
    tx.append(features[inicio: i+n_patches])
    ty.append(labels[inicio: i+n_patches])
    inicio = i+n_patches

  return tx, ty

def unpack_tensor(features, labels, n_patches):

  f = []
  l = []

  count = 0
  for i in features:
      for j in i:
        f.append(j)
        count = count + 1

  for i in labels:
      for j in i:
        l.append(j)
        
  return np.array(f), np.array(l)

def double_test(classe_alvo, train_X, train_Y, test_X, test_Y):

    """
      SubSet do Treino e Teste
    """

    # Seleciona os 5 Impostores para o treino
    impostores = list(range(1,81))
    impostores.remove(classe_alvo)
    np.random.shuffle(impostores)
    imp = impostores[:5]
    imp.append(classe_alvo)

    m = [train_Y == i for i in imp]
    mask = ft.reduce(np.logical_or, m)
    train_X = train_X[mask]
    train_Y = train_Y[mask]

    print("\n ------------ len(train_X)")
    print(len(train_X))
    print("\n ------------ train_X[:15")
    print(train_X[:15])

    # Seleciona a classe teste com 5 impostores
    m = [test_Y == i for i in imp]
    mask = ft.reduce(np.logical_or, m)
    test_X_five = test_X[mask]
    test_Y_five = test_Y[mask]

    # Seleciona a classe teste com Todos os impostores
    imp = impostores
    imp.append(classe_alvo)
    m = [test_Y == i for i in imp]
    mask = ft.reduce(np.logical_or, m)
    test_X_all = test_X[mask]
    test_Y_all = test_Y[mask]

    print("\n ------------ test_Y_five")
    print(test_Y_five)
    print("\n ------------ test_Y_all")
    print(test_Y_all)

    # tudo que não for o alvo é impostora = 2
    if (classe_alvo == 2):
      print("\n\n\n ----------------- AAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAAan", classe_alvo)
      train_Y[ train_Y == 1] = 3
      test_Y_five[ test_Y_five == 1] = 3
      test_Y_all[ test_Y_all == 1] = 3

      train_Y[ train_Y == classe_alvo] = 1
      test_Y_five[ test_Y_five == classe_alvo] = 1
      test_Y_all[ test_Y_all == classe_alvo] = 1
      
      train_Y[ train_Y != 1 ] = 2
      test_Y_five[ test_Y_five != 1] = 2
      test_Y_all[ test_Y_all != 1] = 2

    else:
      print("\n\n\n ----------------- BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB ", classe_alvo)

      train_Y[ train_Y != classe_alvo] = 2
      test_Y_five[ test_Y_five != classe_alvo] = 2
      test_Y_all[ test_Y_all != classe_alvo] = 2
      
      train_Y[ train_Y == classe_alvo] = 1
      test_Y_five[ test_Y_five == classe_alvo] = 1
      test_Y_all[ test_Y_all == classe_alvo] = 1

    print("\n ================ IMPOSTORES ")
    print("\n ------------ test_Y_five")
    print(test_Y_five)
    print("\n ------------ test_Y_all")
    print(test_Y_all)

    return train_X, train_Y, test_X_five, test_Y_five, test_X_all, test_Y_all

def get_final_predictions(n_patches, predicted):
    songs = int(predicted.shape[0] / n_patches)

    r = predicted.reshape((songs,n_patches))
    r = [np.unique(i, return_counts=True) for i in r]
    r = [ i[0][np.argmax(i[1])] for i in r]
    
    return r

def get_final_predictions_sumvote(n_patches, predicted, c, d, e, f):
    
    songs = predicted.shape[0]
    n_patches = 1
    
    r = predicted.reshape((songs, n_patches,-1))
    r2 = c.reshape((songs, n_patches,-1))
    r3 = d.reshape((songs, n_patches,-1))
    r4 = e.reshape((songs, n_patches,-1))
    r5 = f.reshape((songs, n_patches,-1))
    out = np.argmax(np.sum(r, 1) + np.sum(r2, 1) + np.sum(r3, 1) + np.sum(r4, 1) + np.sum(r5, 1), -1) + 1
    
    return out


def get_labels(n_patches, labels):
    o = []
    for i in range(0,len(labels),n_patches):
        o.append(labels[i])
    return np.array(o)

def uni_shuffle(a, b):
    assert len(a) == len(b)
    p = np.random.permutation(len(a))
    return a[p], b[p]
    

# Função principal

In [5]:
def run_experiment(validation_test_size, folds, total_patches, proto_x, proto_y):
    sujeitos = {}
    for classe_alvo in range(1,81):
      results = {}
      print("Classe: ", classe_alvo);
      for patches in total_patches:
      #for patches in [3]:
          print("Patch: ", patches)
          results[patches] = {'f1_five' : [], 'f1_all': []}
          for test_fold in folds:
              print(f"\n\n\n+--------------Patches: {patches} ---- Test_fold: {test_fold}")
              train_folds = sorted( list(set(folds) - set([test_fold])) )
              # train_folds = sorted( list(set(folds) - set([1])) )
              # > [2, 3, 4, 5]

              train_X = np.concatenate([np.load(proto_x % (f,patches)) for f in train_folds])
              train_Y = np.concatenate([ np.load(proto_y % (f,patches)) for f in train_folds ])

              test_X = np.load(proto_x % (test_fold,patches))
              test_Y = np.load(proto_y % (test_fold,patches))

              """
                  Fazer um Shuffle com TENSOR
                  [ [ 0,0,0], [0,0,0] , [1,1,1] ]
              """
              train_X, train_Y = get_tensor(train_X,train_Y ,patches)
              train_X, train_Y = shuffle(train_X, train_Y)
              train_X, train_Y = unpack_tensor(train_X, train_Y, patches)

              test_X, test_Y = get_tensor(test_X,test_Y ,patches)
              test_X, test_Y = shuffle(test_X, test_Y)
              test_X, test_Y = unpack_tensor(test_X, test_Y, patches)
              
              """
                SubSet do Treino e Teste
              """
              train_X, train_Y, test_X_five, test_Y_five, test_X_all, test_Y_all = double_test(classe_alvo, train_X, train_Y, test_X, test_Y)


              """
                Normalizar X's
              """
              ss = StandardScaler()
              train_X = ss.fit_transform(train_X)

              test_X_five = ss.transform(test_X_five)
              test_X_all = ss.transform(test_X_all)

              """
                Treino
              """
              params = {'C' : [1, 10, 100, 1000], 'gamma' : ['auto', 2e-1, 2e-2, 2e-3]}
              svm = SVC(probability=True)

              clf = SingleSplitGridSearch(svm, params, test_size=validation_test_size)
              clf.fit(train_X, train_Y)
              print("\n------ Melhor Parametro: ", clf.best_params_)

              """
                Fit Para 5 Impostores
              """
              prob = clf.best_estimator_.predict_proba(test_X_five)    

              l = get_labels(patches, test_Y_five)
              p = get_final_predictions_sumvote(patches, prob)

              f1_five = f1_score(l, p, average='weighted')
              print("-------------- F1_Score --- FIVE: ",f1_five)

              """
                Fit Para TODOS Impostores
              """
              prob = clf.best_estimator_.predict_proba(test_X_all)    

              l = get_labels(patches, test_Y_all)
              p = get_final_predictions_sumvote(patches, prob)

              f1_all = f1_score(l, p, average='weighted')
              print("-------------- F1_Score --- ALL: ",f1_all)

              results[patches]['f1_five'].append(f1_five)
              results[patches]['f1_all'].append(f1_all)

              sys.stdout.flush()

      print("+------------------------------------\n")
      sujeitos[classe_alvo] = results
    return sujeitos
               
      

# Main

In [19]:
def run():
    escolhas = [  ['BSIF/', 'BSIF_Folder%d_%dx1'], ['LBP/', 'LBP_Folder%d_%dx1'], ['LPQ/','LPQFolder%d_%dx1'], ['MobileNet/', 'commonvoicev1_Fold%d_%dx1'], ['VGG16/', 'commonvoicev1_Fold%d_%dx1'] ]

    for choice in escolhas:
        features_folder = '../datasets/'+choice[0]


        output_proto = features_folder + choice[1]
        
        results = run_experiment(0.25, 
          folds, 
          patches, 
          output_proto + "_X.npy", 
          output_proto + "_Y.npy")
        
        print("results")

        np.save(f'resultados_npy/{choice[0].replace("/", "")}.npy', [results], allow_pickle=True) 

        pprint.pprint(results)

In [20]:
run()

Classe:  1
Patch:  1



+--------------Patches: 1 ---- Test_fold: 1

 ------------ len(train_X)
24

 ------------ train_X[:15
[[0.004922 0.001441 0.002253 ... 0.009925 0.001548 0.001913]
 [0.001743 0.000346 0.000535 ... 0.004494 0.000434 0.00051 ]
 [0.005035 0.001171 0.00214  ... 0.011845 0.001863 0.001957]
 ...
 [0.005035 0.000818 0.001334 ... 0.009592 0.00141  0.001863]
 [0.003525 0.000415 0.000705 ... 0.005998 0.000617 0.000755]
 [0.00472  0.000642 0.001303 ... 0.009932 0.001529 0.001492]]

 ------------ test_Y_five
[ 1 61 62 77 23 17]

 ------------ test_Y_all
[59 64 30 46  1 15 41 66 79 31 61 72 10 29 20 57 33 45 43 44 62 55 25 73
 58 67 13 19 65  7 36  8 42  9 11 39 12  4 74 54 48 26  3 38 27  6 75 32
 47 77 51 35 53 52 24 34 40 37 71 56 18 28 76  2 21 22 68 23 16 49 69 50
 80 17 14  5 78 63 70 60]



 ----------------- BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB  1

 ================ IMPOSTORES 

 ------------ test_Y_five
[1 2 2 2 2 2]

 ------------ test_Y_all
[2 2 2 2 




+--------------Patches: 3 ---- Test_fold: 2

 ------------ len(train_X)
72

 ------------ train_X[:15
[[0.001892 0.000328 0.000232 ... 0.002953 0.000251 0.000502]
 [0.00608  0.001119 0.001795 ... 0.011735 0.001776 0.001679]
 [0.004297 0.001017 0.002609 ... 0.01059  0.001957 0.002206]
 ...
 [0.002258 0.000251 0.000347 ... 0.003706 0.000386 0.000232]
 [0.005076 0.000676 0.001158 ... 0.010268 0.00139  0.001216]
 [0.005084 0.00142  0.001132 ... 0.011741 0.00188  0.001765]]

 ------------ test_Y_five
[ 6  6  6 21 21 21  1  1  1 53 53 53 40 40 40 80 80 80]

 ------------ test_Y_all
[69 69 69 56 56 56 67 67 67 68 68 68 31 31 31 57 57 57 38 38 38 39 39 39
 44 44 44 51 51 51 76 76 76 36 36 36 52 52 52 41 41 41 22 22 22  6  6  6
 30 30 30 71 71 71 25 25 25 49 49 49 46 46 46 21 21 21  1  1  1 53 53 53
 40 40 40 29 29 29 28 28 28 45 45 45 24 24 24 32 32 32 42 42 42 10 10 10
 77 77 77 12 12 12  8  8  8 58 58 58 14 14 14 11 11 11 72 72 72 47 47 47
 26 26 26 75 75 75 61 61 61 35 35 35  5  5  5 34 


------ Melhor Parametro:  {'C': 1, 'gamma': 'auto'}
-------------- F1_Score --- FIVE:  0.7575757575757575
-------------- F1_Score --- ALL:  0.9812893081761006
Patch:  5



+--------------Patches: 5 ---- Test_fold: 1

 ------------ len(train_X)
120

 ------------ train_X[:15
[[0.006436 0.002389 0.002223 ... 0.0138   0.002057 0.001592]
 [0.005947 0.001625 0.00494  ... 0.012804 0.002795 0.00377 ]
 [0.003907 0.000985 0.002791 ... 0.008832 0.002167 0.003053]
 ...
 [0.006829 0.000854 0.001313 ... 0.010999 0.000919 0.002561]
 [0.006012 0.00039  0.000292 ... 0.010919 0.000975 0.000682]
 [0.008011 0.00046  0.000952 ... 0.009291 0.000657 0.001215]]

 ------------ test_Y_five
[29 29 29 29 29 56 56 56 56 56 23 23 23 23 23 10 10 10 10 10 80 80 80 80
 80  1  1  1  1  1]

 ------------ test_Y_all
[44 44 44 44 44 58 58 58 58 58 49 49 49 49 49 73 73 73 73 73 54 54 54 54
 54 25 25 25 25 25 29 29 29 29 29 47 47 47 47 47 41 41 41 41 41 18 18 18
 18 18  2  2  2  2  2 55 55 55 55 55 26 26 26 26 26 56 56 56


------ Melhor Parametro:  {'C': 1, 'gamma': 'auto'}
-------------- F1_Score --- FIVE:  0.7575757575757575
-------------- F1_Score --- ALL:  0.9812893081761006



+--------------Patches: 5 ---- Test_fold: 4

 ------------ len(train_X)
120

 ------------ train_X[:15
[[0.005175 0.000929 0.002156 ... 0.012175 0.001095 0.00136 ]
 [0.009164 0.001722 0.002177 ... 0.016703 0.002015 0.001755]
 [0.010703 0.0022   0.004268 ... 0.020225 0.002397 0.00348 ]
 ...
 [0.005417 0.000722 0.001182 ... 0.010047 0.001346 0.001576]
 [0.006857 0.000585 0.000682 ... 0.012609 0.000877 0.001267]
 [0.008405 0.003415 0.005778 ... 0.020816 0.004761 0.00591 ]]

 ------------ test_Y_five
[32 32 32 32 32 42 42 42 42 42  1  1  1  1  1 23 23 23 23 23 62 62 62 62
 62 55 55 55 55 55]

 ------------ test_Y_all
[26 26 26 26 26 74 74 74 74 74 40 40 40 40 40  2  2  2  2  2 11 11 11 11
 11 21 21 21 21 21 56 56 56 56 56 39 39 39 39 39 41 41 41 41 41 32 32 32
 32 32 31 31 31 31 31 76 76 76 76 76 24 24 24 24 24 25 25 25 25 25 17 


------ Melhor Parametro:  {'C': 100, 'gamma': 0.02}
-------------- F1_Score --- FIVE:  0.7575757575757575
-------------- F1_Score --- ALL:  0.975



+--------------Patches: 10 ---- Test_fold: 2

 ------------ len(train_X)
240

 ------------ train_X[:15
[[0.003397 0.000425 0.000566 ... 0.004671 0.000283 0.000566]
 [0.004985 0.000969 0.000554 ... 0.011216 0.001662 0.001523]
 [0.007996 0.002168 0.001762 ... 0.015856 0.002981 0.002575]
 ...
 [0.003659 0.000271 0.000813 ... 0.008199 0.000745 0.000813]
 [0.002562 0.000208 0.001246 ... 0.007062 0.000692 0.000692]
 [0.003669 0.000277 0.001385 ... 0.008377 0.001038 0.001731]]

 ------------ test_Y_five
[ 8  8  8  8  8  8  8  8  8  8  1  1  1  1  1  1  1  1  1  1 24 24 24 24
 24 24 24 24 24 24 55 55 55 55 55 55 55 55 55 55 27 27 27 27 27 27 27 27
 27 27 72 72 72 72 72 72 72 72 72 72]

 ------------ test_Y_all
[74 74 74 74 74 74 74 74 74 74 54 54 54 54 54 54 54 54 54 54 77 77 77 77
 77 77 77 77 77 77 16 16 16 16 16 16 16 16 16 16 80 80 80 80 80 

...


------ Melhor Parametro:  {'C': 10, 'gamma': 0.002}
-------------- F1_Score --- FIVE:  0.7083333333333334
-------------- F1_Score --- ALL:  0.9081213307240702
Patch:  5



+--------------Patches: 5 ---- Test_fold: 1

 ------------ len(train_X)
120

 ------------ train_X[:15
[[5.6400e-04 1.0000e-04 1.0000e-04 ... 9.2900e-04 3.3000e-05 1.3300e-04]
 [2.1770e-03 2.2700e-04 3.9000e-04 ... 5.4920e-03 7.1500e-04 7.8000e-04]
 [8.1420e-03 8.8600e-04 1.4450e-03 ... 1.5825e-02 1.6740e-03 1.9370e-03]
 ...
 [4.3670e-03 1.4120e-03 1.9370e-03 ... 9.0620e-03 1.7400e-03 2.1010e-03]
 [4.4850e-03 9.4200e-04 1.6250e-03 ... 9.7490e-03 2.0150e-03 2.2420e-03]
 [2.5610e-03 8.5400e-04 1.7400e-03 ... 7.5190e-03 1.6420e-03 1.6090e-03]]

 ------------ test_Y_five
[62 62 62 62 62 64 64 64 64 64 60 60 60 60 60 80 80 80 80 80 79 79 79 79
 79 11 11 11 11 11]

 ------------ test_Y_all
[75 75 75 75 75  5  5  5  5  5 63 63 63 63 63 46 46 46 46 46 65 65 65 65
 65 70 70 70 70 70 73 73 73 73 73 62 62 62 62 62 25 25 25 25 

-------------- F1_Score --- ALL:  0.9812893081761006



+--------------Patches: 5 ---- Test_fold: 4

 ------------ len(train_X)
120

 ------------ train_X[:15
[[0.007099 0.001062 0.002289 ... 0.013568 0.001393 0.00209 ]
 [0.007344 0.00104  0.002307 ... 0.013811 0.002437 0.00338 ]
 [0.006599 0.001346 0.002364 ... 0.016121 0.00197  0.00243 ]
 ...
 [0.006599 0.001313 0.001904 ... 0.01264  0.002495 0.002233]
 [0.008319 0.000682 0.00182  ... 0.011894 0.002177 0.003347]
 [0.006632 0.001642 0.002003 ... 0.008733 0.002495 0.003021]]

 ------------ test_Y_five
[21 21 21 21 21 20 20 20 20 20 80 80 80 80 80 59 59 59 59 59 25 25 25 25
 25 76 76 76 76 76]

 ------------ test_Y_all
[ 3  3  3  3  3 72 72 72 72 72 36 36 36 36 36 40 40 40 40 40  4  4  4  4
  4 61 61 61 61 61 53 53 53 53 53  7  7  7  7  7 45 45 45 45 45 60 60 60
 60 60 12 12 12 12 12 65 65 65 65 65 74 74 74 74 74 34 34 34 34 34 27 27
 27 27 27 21 21 21 21 21 77 77 77 77 77 71 71 71 71 71 66 66 66 66 66 28
 28 28 28 28 32 32 32 32 32 19 


------ Melhor Parametro:  {'C': 10, 'gamma': 'auto'}
-------------- F1_Score --- FIVE:  0.7575757575757575
-------------- F1_Score --- ALL:  0.975



+--------------Patches: 10 ---- Test_fold: 2

 ------------ len(train_X)
240

 ------------ train_X[:15
[[0.000566 0.       0.000142 ... 0.000708 0.       0.      ]
 [0.004016 0.0009   0.000831 ... 0.006993 0.001108 0.000485]
 [0.000474 0.       0.       ... 0.000745 0.       0.      ]
 ...
 [0.00271  0.000136 0.000813 ... 0.004066 0.000542 0.      ]
 [0.000969 0.       0.000138 ... 0.002215 0.000138 0.000277]
 [0.005262 0.000277 0.000415 ... 0.0072   0.001246 0.000554]]

 ------------ test_Y_five
[22 22 22 22 22 22 22 22 22 22 40 40 40 40 40 40 40 40 40 40 61 61 61 61
 61 61 61 61 61 61 80 80 80 80 80 80 80 80 80 80 67 67 67 67 67 67 67 67
 67 67 16 16 16 16 16 16 16 16 16 16]

 ------------ test_Y_all
[27 27 27 27 27 27 27 27 27 27 22 22 22 22 22 22 22 22 22 22 66 66 66 66
 66 66 66 66 66 66  5  5  5  5  5  5  5  5  5  5 53 53 53 53 53


------ Melhor Parametro:  {'C': 100, 'gamma': 'auto'}
-------------- F1_Score --- FIVE:  0.7575757575757575
-------------- F1_Score --- ALL:  0.9812893081761006



+--------------Patches: 10 ---- Test_fold: 4

 ------------ len(train_X)
240

 ------------ train_X[:15
[[0.002548 0.000283 0.       ... 0.002123 0.000283 0.      ]
 [0.003046 0.001246 0.000831 ... 0.009208 0.000969 0.000831]
 [0.003185 0.001355 0.00122  ... 0.009283 0.001084 0.000678]
 ...
 [0.004201 0.000745 0.000271 ... 0.008267 0.003252 0.001287]
 [0.006369 0.001108 0.001246 ... 0.0117   0.001523 0.0018  ]
 [0.007339 0.001939 0.002908 ... 0.015093 0.002077 0.003254]]

 ------------ test_Y_five
[34 34 34 34 34 34 34 34 34 34 12 12 12 12 12 12 12 12 12 12 80 80 80 80
 80 80 80 80 80 80 72 72 72 72 72 72 72 72 72 72  6  6  6  6  6  6  6  6
  6  6  3  3  3  3  3  3  3  3  3  3]

 ------------ test_Y_all
[61 61 61 61 61 61 61 61 61 61 79 79 79 79 79 79 79 79 79 79 74 74 74 74
 74 74 74 74 74 74 28 28 28 28 28 28 28 28 28 28 


------ Melhor Parametro:  {'C': 10, 'gamma': 0.002}
-------------- F1_Score --- FIVE:  0.7575757575757575
-------------- F1_Score --- ALL:  0.9355263157894737
+------------------------------------

results
{1: {1: {'f1_all': [0.9812893081761006,
                    0.9812893081761006,
                    0.9001700680272109,
                    0.9812893081761006,
                    0.9686305732484077],
         'f1_five': [0.7575757575757575,
                     0.7575757575757575,
                     0.6666666666666669,
                     0.7575757575757575,
                     0.7575757575757575]},
     3: {'f1_all': [0.9812893081761006,
                    0.975,
                    0.9812893081761006,
                    0.9812893081761006,
                    0.9812893081761006],
         'f1_five': [0.7575757575757575,
                     0.7575757575757575,
                     0.7575757575757575,
                     0.7575757575757575,
                     0.7575757575